preprocess_daily.py

In [1]:
import pandas as pd
import numpy as np
import os, sys, copy, argparse, json, pickle, sys
import sumolib, traci
from tqdm import tqdm
from datetime import datetime
path_root = os.path.dirname(os.path.dirname(os.path.abspath('.')))
path_scr = os.path.join(path_root, 'scripts')
sys.path.append(path_scr)
from preprocess_daily import DailyPreprocessor
from generate_signals import SignalGenerator

In [2]:
config_name = 'revised'
file_net = 'sn.net.xml'
self = DailyPreprocessor(config_name=config_name, file_net=file_net)

In [3]:
self.main()

1. 데이터를 로드합니다.
1-1. 네트워크가 로드되었습니다.
1-2. 테이블들이 로드되었습니다.
1-3. 네트워크의 모든 clean state requirement들을 체크했습니다.
1-5. 테이블을 표준화했습니다.
1-6. 주요 객체 (리스트, 딕셔너리)들을 저장했습니다.
2. 중간산출물을 생성합니다.
2-1. 매칭 테이블들을 생성했습니다.
2-2. 초기화 신호가 지정되었습니다. (우회전 : g)
2-3. 유턴 인덱스 / 비보호좌회전 인덱스를 지정했습니다.
2-4. 직진 및 좌회전(G)을 배정했습니다.
2-5. node2num_cycles.json를 저장했습니다.
3. 이슈사항을 저장합니다.


In [4]:
self = SignalGenerator()
self.main()

1. 데이터를 준비합니다.
1-1. 네트워크가 로드되었습니다.
1-2. 테이블들이 로드되었습니다.
1-5. 필요한 보조 객체들이 모두 준비되었습니다.
2. 신호이력 테이블을 변환합니다.
3. 이동류정보 테이블을 변환합니다.
4. 통합 테이블을 생성합니다.
5. 신호를 생성합니다.
6. 이슈사항을 저장합니다.
(1) 0:00:01.848446
(1-1) 0:00:01.781893
(1-2) 0:00:00.050542
(1-3) 0:00:00
(1-4) 0:00:00
(1-5) 0:00:00.016011
(2) 0:00:00.032995
(2-1) 0:00:00.015911
(2-2) 0:00:00.017084
(2-3) 0:00:00
(3) 0:00:00.262816
(3-1) 0:00:00.259815
(3-2) 0:00:00.003001
(4) 0:00:00.037998
(4-1) 0:00:00.000926
(4-2) 0:00:00.002999
(4-2) 0:00:00.034073
(5) 0:00:00.270916
(5-1) 0:00:00.003018
(5-2) 0:00:00.265888
(5-3) 0:00:00.002010
(6) 0:00:00
total time : 0:00:02.453171


c:\github\siggen\scripts\generate_signals.py:693: FutureWarning: DataFrame.fillna with 'method' is deprecated and will raise in a future version. Use obj.ffill() or obj.bfill() instead.
  SIG[['phas_A', 'state_A']] = SIG[['phas_A', 'state_A']].fillna(method='ffill')
c:\github\siggen\scripts\generate_signals.py:694: FutureWarning: DataFrame.fillna with 'method' is deprecated and will raise in a future version. Use obj.ffill() or obj.bfill() instead.
  SIG[['phas_B', 'state_B']] = SIG[['phas_B', 'state_B']].fillna(method='ffill')
c:\github\siggen\scripts\generate_signals.py:693: FutureWarning: DataFrame.fillna with 'method' is deprecated and will raise in a future version. Use obj.ffill() or obj.bfill() instead.
  SIG[['phas_A', 'state_A']] = SIG[['phas_A', 'state_A']].fillna(method='ffill')
c:\github\siggen\scripts\generate_signals.py:694: FutureWarning: DataFrame.fillna with 'method' is deprecated and will raise in a future version. Use obj.ffill() or obj.bfill() instead.
  SIG[['phas_

In [4]:
self.uturn = pd.merge(self.uturn, self.u_condition, on='child_id')

# p2inc_edge2angle : node_id to inc_edge2angle
p2inc_edge2angle = dict()
# p2out_edge2angle : node_id to out_edge2angle
p2out_edge2angle = dict()
# p2inc_angle2edge : node_id to inc_angle2edge
p2inc_angle2edge = dict()
# p2out_angle2edge : node_id to out_angle2edge
p2out_angle2edge = dict()
for node_id in self.parent_ids:
    m5 = self.match5[self.match5.node_id==node_id]
    m5 = m5.dropna(subset=['inc_edge_id', 'out_edge_id'])
    # inc_edge2angle : inc_edge_id to inc_angle
    inc_edge2angle = dict(zip(m5.inc_edge_id, m5.inc_angle.astype(int)))
    p2inc_edge2angle[node_id] = inc_edge2angle
    # out_edge2angle : out_edge_id to out_angle
    out_edge2angle = dict(zip(m5.out_edge_id, m5.out_angle.astype(int)))
    p2out_edge2angle[node_id] = out_edge2angle
    # inc_angle2edge : inc_angle to inc_edge_id
    inc_angle2edge = dict(zip(m5.inc_angle.astype(int), m5.inc_edge_id))
    p2inc_angle2edge[node_id] = inc_angle2edge
    # out_angle2edge : out_angle to out_edge_id
    out_angle2edge = dict(zip(m5.out_angle.astype(int), m5.out_edge_id))
    p2out_angle2edge[node_id] = out_angle2edge

In [5]:
cmatches = []
row = self.uturn.iloc[0]
parent_id = row.parent_id
child_id = row.child_id
condition = row.condition
inc_edge_id = row.inc_edge_id
out_edge_id = row.out_edge_id
adj_inc_edge_id = row.adj_inc_edge_id
adj_out_edge_id = row.adj_out_edge_id

# match5에서 부모노드id에 해당하는 행들을 가져옴 (cmatch)
cmatch = self.match5.copy()[self.match5.node_id==parent_id] # match dataframe for a child node
cmatch = cmatch.sort_values(by=['phase_no', 'ring_type']).reset_index(drop=True)
cmatch['node_id'] = child_id
cmatch['node_type'] = 'u_turn'

# 진입엣지 각도
inc_angle = p2inc_edge2angle[parent_id][adj_inc_edge_id]

# 이격각도
self.angle_separation = 10

# 진입로 각도 목록
inc_angles = cmatch.dropna(subset=['inc_angle', 'out_angle']).inc_angle.astype(int).unique()
inc_angles = np.sort(inc_angles)
inc_angles = list(inc_angles - 360) + list(inc_angles) + list(inc_angles + 360)
inc_angles = np.array(inc_angles)

# 보행신호시의 진입로 각도
inc_angles_left = inc_angles[inc_angles >= inc_angle + self.angle_separation]
inc_angle_pedes = np.sort(inc_angles_left)[0] % 360

# 보행신호시의 진입로 엣지id
inc_angle2edge = p2inc_angle2edge[parent_id]
inc_edge_id_pedes = inc_angle2edge[inc_angle_pedes]

# 진출로 각도 목록
out_angles = cmatch.dropna(subset=['inc_angle', 'out_angle']).out_angle.astype(int).unique()
out_angles = np.sort(out_angles)
out_angles = list(out_angles - 360) + list(out_angles) + list(out_angles + 360)
out_angles = np.array(out_angles)

# 보행신호시의 진출로 각도
out_angles_right = out_angles[out_angles <= inc_angle - self.angle_separation]
out_angle_pedes = np.sort(out_angles_right)[-1] % 360

# 보행신호시의 진출로 엣지id
out_angle2edge = p2out_angle2edge[parent_id]
out_edge_id_pedes = out_angle2edge[out_angle_pedes]

# 진입엣지/진출엣지 포함 조건
inc_true = (cmatch.inc_edge_id==adj_inc_edge_id)
out_true = (cmatch.out_edge_id==adj_out_edge_id)

# 보행신호시 조건
pedes_flag = (cmatch.inc_edge_id==inc_edge_id_pedes) & (cmatch.out_edge_id==out_edge_id_pedes)

# 좌회전시 조건
right_flag = inc_true & (cmatch.turn_type=='left')

# 보행신호이동류(17) 조건
crosswalk_on = (cmatch.move_no==17) & ~ out_true

# 신호없음이동류(18) 조건
all_redsigns = (cmatch.move_no==18) & ~ out_true

In [6]:
print(cmatch)

   inter_no  phase_no ring_type  move_no inc_dire out_dire inc_angle  \
0       175         1         A        8        남        북       179   
1       175         1         B        4        북        남       003   
2       175         2         A        7        북        동       001   
3       175         2         B        3        남        서       179   
4       175         3         A        6        동        서       092   
5       175         3         B        1        동        남       090   
6       175         4         A        5        서        북       268   
7       175         4         B        2        서        동       270   

  out_angle    inc_edge_id   out_edge_id node_id node_type turn_type  
0       004  -571542797_02  571500487_01     u00    u_turn  straight  
1       176  -571500487_01  571542797_02     u00    u_turn  straight  
2       095  -571500487_01  571545870_01     u00    u_turn      left  
3       271  -571542797_02  571510153_01     u00    u_turn      lef

In [9]:
cmatch[['inc_edge_id', 'out_edge_id']]

inc_edge_id   out_edge_id
0  -571542797_02  571500487_01
1  -571500487_01  571542797_02
2  -571500487_01  571545870_01
3  -571542797_02  571510153_01
4   571545870_02  571510153_01
5   571545870_02  571542797_02
6   571510153_02  571500487_01
7   571510153_02  571545870_01

In [13]:
cmatch[['inc_edge_id', 'out_edge_id']] = cmatch[['inc_edge_id', 'out_edge_id']].astype('object')

inc_edge_id      out_edge_id
0           NaN              NaN
1           NaN              NaN
2  571500487_02  571500487_01.32
3           NaN              NaN
4           NaN              NaN
5           NaN              NaN
6           NaN              NaN
7           NaN              NaN

In [10]:
# 보행신호시/좌회전시 진입/진출 엣지id 배정
cmatch[['inc_edge_id', 'out_edge_id']] = None
if condition == "보행신호시":
    cmatch.loc[pedes_flag, ['inc_edge_id', 'out_edge_id']] = [inc_edge_id, out_edge_id]
elif condition == "좌회전시":
    cmatch.loc[right_flag, ['inc_edge_id', 'out_edge_id']] = [inc_edge_id, out_edge_id]

In [37]:
# 각 uturn node에 대하여 (inc_edge_id, out_edge_id) 부여
cmatches = []
for row in self.uturn.itertuples():
    parent_id = row.parent_id
    child_id = row.child_id
    condition = row.condition
    inc_edge_id = row.inc_edge_id
    out_edge_id = row.out_edge_id
    adj_inc_edge_id = row.adj_inc_edge_id
    adj_out_edge_id = row.adj_out_edge_id
    
    # match5에서 부모노드id에 해당하는 행들을 가져옴 (cmatch)
    cmatch = self.match5.copy()[self.match5.node_id==parent_id] # match dataframe for a child node
    cmatch = cmatch.sort_values(by=['phase_no', 'ring_type']).reset_index(drop=True)
    cmatch['node_id'] = child_id
    cmatch['node_type'] = 'u_turn'

    # 진입엣지 각도
    inc_angle = p2inc_edge2angle[parent_id][adj_inc_edge_id]

    # 이격각도
    self.angle_separation = 10

    # 진입로 각도 목록
    inc_angles = cmatch.dropna(subset=['inc_angle', 'out_angle']).inc_angle.astype(int).unique()
    inc_angles = np.sort(inc_angles)
    inc_angles = list(inc_angles - 360) + list(inc_angles) + list(inc_angles + 360)
    inc_angles = np.array(inc_angles)

    # 보행신호시의 진입로 각도
    inc_angles_left = inc_angles[inc_angles >= inc_angle + self.angle_separation]
    inc_angle_pedes = np.sort(inc_angles_left)[0] % 360

    # 보행신호시의 진입로 엣지id
    inc_angle2edge = p2inc_angle2edge[parent_id]
    inc_edge_id_pedes = inc_angle2edge[inc_angle_pedes]

    # 진출로 각도 목록
    out_angles = cmatch.dropna(subset=['inc_angle', 'out_angle']).out_angle.astype(int).unique()
    out_angles = np.sort(out_angles)
    out_angles = list(out_angles - 360) + list(out_angles) + list(out_angles + 360)
    out_angles = np.array(out_angles)

    # 보행신호시의 진출로 각도
    out_angles_right = out_angles[out_angles <= inc_angle - self.angle_separation]
    out_angle_pedes = np.sort(out_angles_right)[-1] % 360

    # 보행신호시의 진출로 엣지id
    out_angle2edge = p2out_angle2edge[parent_id]
    out_edge_id_pedes = out_angle2edge[out_angle_pedes]

    # 진입엣지/진출엣지 포함 조건
    inc_true = (cmatch.inc_edge_id==adj_inc_edge_id)
    out_true = (cmatch.out_edge_id==adj_out_edge_id)

    # 보행신호시 조건
    pedes_flag = (cmatch.inc_edge_id==inc_edge_id_pedes) & (cmatch.out_edge_id==out_edge_id_pedes)

    # 좌회전시 조건
    right_flag = inc_true & (cmatch.turn_type=='left')

    # 보행신호이동류(17) 조건
    crosswalk_on = (cmatch.move_no==17) & ~ out_true

    # 신호없음이동류(18) 조건
    all_redsigns = (cmatch.move_no==18) & ~ out_true

    # 보행신호시/좌회전시 진입/진출 엣지id 배정
    cmatch[['inc_edge_id', 'out_edge_id']] = np.nan
    if condition == "보행신호시":
        cmatch.loc[pedes_flag, ['inc_edge_id', 'out_edge_id']] = [inc_edge_id, out_edge_id]
    elif condition == "좌회전시":
        cmatch.loc[right_flag, ['inc_edge_id', 'out_edge_id']] = [inc_edge_id, out_edge_id]

    uturn_not_assigned = cmatch[['inc_edge_id','out_edge_id']].isna().any(axis=1).all()

    if uturn_not_assigned:
        # 좌회전시
        if right_flag.any():
            cmatch.loc[right_flag, ['inc_edge_id', 'out_edge_id']] = [inc_edge_id, out_edge_id]
        # 보행신호시
        elif pedes_flag.any():
            cmatch.loc[pedes_flag, ['inc_edge_id', 'out_edge_id']] = [inc_edge_id, out_edge_id]
        # 보행신호이동류(17) 발생시
        elif crosswalk_on.any():
            cmatch.loc[crosswalk_on, ['inc_edge_id', 'out_edge_id']] = [inc_edge_id, out_edge_id]
        # 신호없음이동류(18) 발생시
        elif all_redsigns.any():
            cmatch.loc[all_redsigns, ['inc_edge_id', 'out_edge_id']] = [inc_edge_id, out_edge_id]
        # 진출엣지 미포함시
        elif out_true.any():
            cmatch.loc[~ out_true, ['inc_edge_id', 'out_edge_id']] = [inc_edge_id, out_edge_id]
    cmatches.append(cmatch)

C:\Users\Uinetworks\AppData\Local\Temp\ipykernel_18920\3718306561.py:73: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise an error in a future version of pandas. Value '571500487_02' has dtype incompatible with float64, please explicitly cast to a compatible dtype first.
  cmatch.loc[right_flag, ['inc_edge_id', 'out_edge_id']] = [inc_edge_id, out_edge_id]
C:\Users\Uinetworks\AppData\Local\Temp\ipykernel_18920\3718306561.py:73: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise an error in a future version of pandas. Value '571500487_01.32' has dtype incompatible with float64, please explicitly cast to a compatible dtype first.
  cmatch.loc[right_flag, ['inc_edge_id', 'out_edge_id']] = [inc_edge_id, out_edge_id]
C:\Users\Uinetworks\AppData\Local\Temp\ipykernel_18920\3718306561.py:71: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise an error in a future version of pandas. Value '571542810_01.

In [ ]:

# 각 연등교차로(coordination node)에 대하여 (inc_edge_id, out_edge_id) 부여
self.coord['inter_no'] = self.coord['parent_id'].map(self.node2inter)
self.coord = self.coord.rename(columns={'child_id':'node_id'})
self.coord[['inc_dire', 'out_dire', 'inc_angle','out_angle']] = np.nan
self.coord['move_no'] = 20
self.coord = self.coord[['inter_no', 'phase_no', 'ring_type', 'move_no', 'inc_dire', 'out_dire', 'inc_angle','out_angle', 'inc_edge_id', 'out_edge_id', 'node_id']]
self.coord['node_type'] = 'coord'

cmatches = pd.concat(cmatches)
self.match6 = pd.concat([self.match5, cmatches, self.coord]).drop_duplicates().sort_values(by=['inter_no', 'node_id', 'phase_no', 'ring_type'])
self.match6 = self.match6.reset_index(drop=True)
